In [1]:
!pip install open3d

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 408.6 MB 33 kB/s 
     |████████████████████████████████| 1.1 MB 74.9 MB/s 
     |████████████████████████████████| 3.1 MB 72.3 MB/s 
     |████████████████████████████████| 8.8 MB 58.5 MB/s 
     |████████████████████████████████| 423 kB 74.1 MB/s 
     |████████████████████████████████| 54 kB 3.2 MB/s 
     |████████████████████████████████| 9.7 MB 52.6 MB/s 
     |████████████████████████████████| 344 kB 79.8 MB/s 
     |████████████████████████████████| 1.6 MB 66.7 MB/s 
     |████████████████████████████████| 1.2 MB 67.0 MB/s 
     |████████████████████████████████| 59 kB 8.4 MB/s 
     |████████████████████████████████| 80 kB 8.6 MB/s 
     |████████████████████████████████| 55 kB 4.3 MB/s 
     |████████████████████████████████| 271 kB 80.2 MB/s 
     |████████████████████████████████| 133 kB 66.8 MB/s 
     |████████████████████████████████|

In [2]:
import numpy as np
import open3d as o3d
import plotly.graph_objects as go
import matplotlib.pyplot as plt

# Surface Reconstruction Tutorial

In [3]:
def draw_geometries(geometries):
    graph_objects = []

    for geometry in geometries:
        geometry_type = geometry.get_geometry_type()
        
        if geometry_type == o3d.geometry.Geometry.Type.PointCloud:
            points = np.asarray(geometry.points)
            colors = None
            if geometry.has_colors():
                colors = np.asarray(geometry.colors)
            elif geometry.has_normals():
                colors = (0.5, 0.5, 0.5) + np.asarray(geometry.normals) * 0.5
            else:
                geometry.paint_uniform_color((1.0, 0.0, 0.0))
                colors = np.asarray(geometry.colors)

            scatter_3d = go.Scatter3d(x=points[:,0], y=points[:,1], z=points[:,2], mode='markers', marker=dict(size=1, color=colors))
            graph_objects.append(scatter_3d)

        if geometry_type == o3d.geometry.Geometry.Type.TriangleMesh:
            triangles = np.asarray(geometry.triangles)
            vertices = np.asarray(geometry.vertices)
            colors = None
            if geometry.has_triangle_normals():
                colors = (0.5, 0.5, 0.5) + np.asarray(geometry.triangle_normals) * 0.5
                colors = tuple(map(tuple, colors))
            else:
                colors = (1.0, 0.0, 0.0)
            
            mesh_3d = go.Mesh3d(x=vertices[:,0], y=vertices[:,1], z=vertices[:,2], i=triangles[:,0], j=triangles[:,1], k=triangles[:,2], facecolor=colors, opacity=0.50)
            graph_objects.append(mesh_3d)
        
    fig = go.Figure(
        data=graph_objects,
        layout=dict(
            scene=dict(
                xaxis=dict(visible=False),
                yaxis=dict(visible=False),
                zaxis=dict(visible=False)
            )
        )
    )
    fig.show()
o3d.visualization.draw_geometries = draw_geometries

In [4]:
bunny = o3d.data.BunnyMesh()
mesh = o3d.io.read_triangle_mesh(bunny.path)
mesh.compute_vertex_normals()

pcd = mesh.sample_points_poisson_disk(750)
o3d.visualization.draw_geometries([pcd])
alpha = 0.02
print(f"alpha={alpha:.3f}")
mesh = o3d.geometry.TriangleMesh.create_from_point_cloud_alpha_shape(pcd, alpha)
mesh.compute_vertex_normals()
o3d.visualization.draw_geometries([mesh])

[Open3D INFO] Downloading https://github.com/isl-org/open3d_downloads/releases/download/20220201-data/BunnyMesh.ply
[Open3D INFO] Downloaded to /root/open3d_data/download/BunnyMesh/BunnyMesh.ply


alpha=0.020


In [5]:
radii = [0.005, 0.01, 0.02, 0.04]
rec_mesh = o3d.geometry.TriangleMesh.create_from_point_cloud_ball_pivoting(
    pcd, o3d.utility.DoubleVector(radii))
o3d.visualization.draw_geometries([pcd, rec_mesh])

In [6]:
with o3d.utility.VerbosityContextManager(
        o3d.utility.VerbosityLevel.Debug) as cm:
    mesh, densities = o3d.geometry.TriangleMesh.create_from_point_cloud_poisson(
        pcd, depth=9)
print(mesh)
o3d.visualization.draw_geometries([mesh])

[Open3D DEBUG] Input Points / Samples: 750 / 750
[Open3D DEBUG] #   Got kernel density: 0.0111852 (s), 280.684 (MB) / 280.684 (MB) / 280 (MB)
[Open3D DEBUG] #     Got normal field: 0.0123599 (s), 283.133 (MB) / 283.133 (MB) / 283 (MB)
[Open3D DEBUG] Point weight / Estimated Area: 3.890125e-03 / 2.917594e+00
[Open3D DEBUG] #       Finalized tree: 0.0426321 (s), 288.527 (MB) / 288.527 (MB) / 288 (MB)
[Open3D DEBUG] #  Set FEM constraints: 0.152389 (s), 288.527 (MB) / 288.527 (MB) / 288 (MB)
[Open3D DEBUG] #Set point constraints: 0.00384498 (s), 288.527 (MB) / 288.527 (MB) / 288 (MB)
[Open3D DEBUG] Leaf Nodes / Active Nodes / Ghost Nodes: 138083 / 66888 / 90921
[Open3D DEBUG] Memory Usage: 288.527 MB
[Open3D DEBUG] # Linear system solved: 0.100374 (s), 288.527 (MB) / 288.527 (MB) / 288 (MB)
[Open3D DEBUG] Got average: 0.00346613 (s), 288.527 (MB) / 288.527 (MB) / 288 (MB)
[Open3D DEBUG] Iso-Value: 5.023997e-01 = 3.767998e+02 / 7.500000e+02
[Open3D DEBUG] #          Total Solve:       0.8 

# Surface Reconstruction from ARCore's point clouds

In [7]:
from sklearn.preprocessing import MinMaxScaler
def reshapePointCloudData(pointCloud):
  column=6
  row=int(pointCloud.shape[0]/column)
  pointCloud=np.reshape(pointCloud,(row,column))
  pointCloud=pointCloud[~np.all(pointCloud == 0, axis=1)]
  pointCloud=np.hsplit(pointCloud, 2)
  scaler = MinMaxScaler()
  pointCloud[1]=scaler.fit_transform(pointCloud[1])
  return pointCloud[0],pointCloud[1]
def constructPointCloud(numOfImage):
  rawDepthPointCloudData=[]
  for i in range(numOfImage):
    tempData= np.fromfile("rawDepthPointCloudData ("+str(i)+").txt", dtype = np.float32)
    tempData=reshapePointCloudData(tempData)
    print('tempData.shape ',tempData.shape)
    if(rawDepthPointCloudData==[]):
      rawDepthPointCloudData=tempData
    else:
      rawDepthPointCloudData=np.vstack((rawDepthPointCloudData,tempData))

  return rawDepthPointCloudData

In [11]:
rawDepthPointCloudData= np.fromfile("rawDepthPointCloudData.txt", dtype = np.float32)
pointcloud,rgb=reshapePointCloudData(rawDepthPointCloudData)
print(pointcloud)
print(rgb)

[[ 0.29846922 -0.837816   -1.6183815 ]
 [ 0.29966652 -0.84528947 -1.5985832 ]
 [ 0.3008945  -0.8532034  -1.5810442 ]
 ...
 [ 0.03431636 -0.83974445 -0.2563203 ]
 [ 0.06581539 -0.8214816  -0.25778678]
 [ 0.07461035 -0.82229155 -0.25614065]]
[[0.12019231 0.10191083 0.06164384]
 [0.13461539 0.12738854 0.09589041]
 [0.13461539 0.12101911 0.07534246]
 ...
 [0.5865385  0.7388535  0.7328767 ]
 [0.45673078 0.5923567  0.5479452 ]
 [0.6057693  0.7197453  0.71232873]]


In [9]:
pointcloud.shape

(32524, 3)

In [ ]:
pointcloud

array([[ 0.1679545 ,  0.14687884, -1.6713643 ],
       [ 0.16831213,  0.13817823, -1.6793586 ],
       [ 0.1697703 ,  0.12843853, -1.6810707 ],
       ...,
       [ 0.2690692 , -0.49839604, -0.32933098],
       [ 0.273279  , -0.5014457 , -0.32782644],
       [ 0.35891458, -0.5563771 , -0.29864922]], dtype=float32)

In [12]:
pcd = o3d.geometry.PointCloud()
pcd.points = o3d.utility.Vector3dVector(pointcloud)
pcd.colors = o3d.utility.Vector3dVector(rgb)
o3d.visualization.draw_geometries([pcd])

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
alpha = 0.02
print(f"alpha={alpha:.3f}")
mesh = o3d.geometry.TriangleMesh.create_from_point_cloud_alpha_shape(pcd, alpha)
mesh.compute_vertex_normals()
o3d.visualization.draw_geometries([mesh])

alpha=0.020


In [ ]:
radii = [0.005, 0.01, 0.02, 0.04]
pcd.estimate_normals(
    search_param=o3d.geometry.KDTreeSearchParamHybrid(radius=0.1, max_nn=30))
rec_mesh = o3d.geometry.TriangleMesh.create_from_point_cloud_ball_pivoting(
    pcd, o3d.utility.DoubleVector(radii))
o3d.visualization.draw_geometries([rec_mesh])

In [ ]:
rgb

array([[0.55378485, 0.5183673 , 0.45344132],
       [0.5298805 , 0.5020408 , 0.4291498 ],
       [0.49402392, 0.47346938, 0.39271256],
       ...,
       [0.5298805 , 0.48979586, 0.4331984 ],
       [0.53386456, 0.48979586, 0.4331984 ],
       [0.5378486 , 0.49795914, 0.4331984 ]], dtype=float32)

In [ ]:
rgb

array([[0.55378485, 0.5183673 , 0.45344132],
       [0.5298805 , 0.5020408 , 0.4291498 ],
       [0.49402392, 0.47346938, 0.39271256],
       ...,
       [0.5298805 , 0.48979586, 0.4331984 ],
       [0.53386456, 0.48979586, 0.4331984 ],
       [0.5378486 , 0.49795914, 0.4331984 ]], dtype=float32)

In [ ]:
rec_mesh.vertex_colors=o3d.utility.Vector3dVector(rgb)

In [ ]:
np.asarray(rec_mesh.vertex_colors)

array([[0.55378485, 0.51836729, 0.45344132],
       [0.52988052, 0.5020408 , 0.42914981],
       [0.49402392, 0.47346938, 0.39271256],
       ...,
       [0.52988052, 0.48979586, 0.43319839],
       [0.53386456, 0.48979586, 0.43319839],
       [0.53784859, 0.49795914, 0.43319839]])

In [ ]:
o3d.visualization.draw_geometries([rec_mesh])

In [ ]:
with o3d.utility.VerbosityContextManager(
        o3d.utility.VerbosityLevel.Debug) as cm:
    mesh, densities = o3d.geometry.TriangleMesh.create_from_point_cloud_poisson(
        pcd, depth=9)
print(mesh)
o3d.visualization.draw_geometries([mesh])

[Open3D DEBUG] Input Points / Samples: 9562 / 9544
[Open3D DEBUG] #   Got kernel density: 0.034961 (s), 322.215 (MB) / 322.215 (MB) / 325 (MB)
[Open3D DEBUG] #     Got normal field: 0.0593121 (s), 322.215 (MB) / 322.215 (MB) / 325 (MB)
[Open3D DEBUG] Point weight / Estimated Area: 7.396286e-05 / 7.072328e-01
[Open3D DEBUG] #       Finalized tree: 0.138491 (s), 323.957 (MB) / 323.957 (MB) / 325 (MB)
[Open3D DEBUG] #  Set FEM constraints: 0.322145 (s), 323.957 (MB) / 323.957 (MB) / 325 (MB)
[Open3D DEBUG] #Set point constraints: 0.0200229 (s), 323.957 (MB) / 323.957 (MB) / 325 (MB)
[Open3D DEBUG] Leaf Nodes / Active Nodes / Ghost Nodes: 247710 / 184440 / 98657
[Open3D DEBUG] Memory Usage: 323.957 MB
[Open3D DEBUG] # Linear system solved: 0.365788 (s), 329.172 (MB) / 329.172 (MB) / 329 (MB)
[Open3D DEBUG] Got average: 0.0163288 (s), 329.172 (MB) / 329.172 (MB) / 329 (MB)
[Open3D DEBUG] Iso-Value: 5.048707e-01 = 4.827573e+03 / 9.562000e+03
[Open3D DEBUG] #          Total Solve:       2.9 (